# Astrophysics III: galaxy formation & evolution
Moodle: https://go.epfl.ch/PHYS-465

## Exercise 13
Teaching assistant: Jonathan Petersson <br>
Email: jonathan.petersson@epfl.ch

***

## Load data:

In [ ]:
import numpy as np
import matplotlib as mpl
import matplotlib.pyplot as plt
from mpl_toolkits.axes_grid1 import make_axes_locatable


%matplotlib inline
plt.rcParams['font.size'] = 14

# Load data:
data        = np.loadtxt('Mbh_Mstellar_box2-bao_144_gas_gt1e10_lumflag.dat')
data = data[data[:,3] != -99]

Mhalo     = data[:,0]
Mstellar  = data[:,1]
Mbh       = data[:,2]
BHAccRate = data[:,3]
CentOrSat = data[:,5]
Nbh       = data[:,6]
SFR       = data[:,7]

## Exercise 13.1

In [ ]:
# Plot:
fig, ax = plt.subplots(2, 2, figsize=(9, 7))

# BH accretion rates:
ax[0,0].hist(np.log10(BHAccRate[BHAccRate > 0]), bins=50, alpha=0.5, rasterized=True)
ax[0,0].hist(np.log10(BHAccRate[(BHAccRate > 0) * (CentOrSat == 0)]), bins=50, alpha=0.5, rasterized=True)
ax[0,0].hist(np.log10(BHAccRate[(BHAccRate > 0) * (CentOrSat == 0) * (Mbh > 1e6)]), bins=50, alpha=0.5, rasterized=True)
ax[0,0].set_yscale('log')
ax[0,0].set_xlabel('$\log_{10}(\dot{M}_\mathrm{BH} \ [\mathrm{M}_\odot \ \mathrm{yr}^{-1}])$')
ax[0,0].set_ylabel('Number of BHs')

# Eddington accretion rate (cgs units):
G         = 6.67e-8
mp        = 1.67262192e-24
epsilon_r = 0.2
c         = 3e10
Thomson   = 6.6524e-25
EddAccRate = (4 * np.pi * G * Mbh * 1.989e33 * mp) / (epsilon_r * c * Thomson)
EddAccRate = EddAccRate / 1.989e33 * 365.25 * 24 * 60 * 60
fedd = BHAccRate / EddAccRate

ax[0,1].hist(np.log10(fedd[BHAccRate > 0]), bins=50, alpha=0.5, rasterized=True)
ax[0,1].hist(np.log10(fedd[(BHAccRate > 0) * (CentOrSat == 0)]), bins=50, alpha=0.5, rasterized=True)
ax[0,1].hist(np.log10(fedd[(BHAccRate > 0) * (CentOrSat == 0) * (Mbh > 1e6)]), bins=50, alpha=0.5, rasterized=True)
ax[0,1].set_yscale('log')
ax[0,1].set_xlabel('$\log_{10}(f_\mathrm{Edd})$')
ax[0,1].set_ylabel('Number of BHs')

# AGN luminosity:
Lbol = epsilon_r * BHAccRate * 1.989e33 / (365.25 * 24 * 60 * 60) * c**2
#Lbol = epsilon_r / (1 - epsilon_r) * BHAccRate * 1.989e33 / (365.25 * 24 * 60 * 60) * c**2
#Ledd = (4 * np.pi * G * Mbh * 1.989e33 * c * mp) / Thomson
#Lbol[fedd < 0.1] = 10 * Ledd[fedd < 0.1] * fedd[fedd < 0.1]**2

ax[1,0].hist(np.log10(Lbol[(Lbol > 1e41) * (BHAccRate > 0)]), bins=50, alpha=0.5, label='All BHs', rasterized=True)
ax[1,0].hist(np.log10(Lbol[(Lbol > 1e41) * (BHAccRate > 0) * (CentOrSat == 0)]), bins=50, alpha=0.5, label='Central BHs', rasterized=True)
ax[1,0].hist(np.log10(Lbol[(Lbol > 1e41) * (BHAccRate > 0) * (CentOrSat == 0) * (Mbh > 1e6)]), bins=50, alpha=0.5, label='Central BHs > $10^6$ M$_\odot$', rasterized=True)
ax[1,0].set_yscale('log')
ax[1,0].set_xlabel('$\log_{10}(L_\mathrm{bol} \ [\mathrm{erg \ s}^{-1}])$')
ax[1,0].set_ylabel('Number of BHs')
fig.tight_layout()
ax[1,0].legend(frameon=False, loc='upper left', bbox_to_anchor=(1, 1))

fig.delaxes(ax[1,1])
fig.savefig('ex1a.pdf')
plt.show()

In [ ]:
# Plot:
fig, ax = plt.subplots(1, 2, figsize=(11, 5), sharex=True, sharey=True)

h = ax[0].hist2d(np.log10(Mbh[BHAccRate > 0]), np.log10(BHAccRate[BHAccRate > 0]), 
                 bins=80, norm=mpl.colors.LogNorm( vmin=1, vmax=1e3), cmap='plasma', rasterized=True)
h = ax[1].hist2d(np.log10(Mbh[(BHAccRate > 0) * (CentOrSat == 0)]), np.log10(BHAccRate[(BHAccRate > 0) * (CentOrSat == 0)]), 
                 bins=80, norm=mpl.colors.LogNorm(vmin=1, vmax=1e3), cmap='plasma', rasterized=True)

ax[0].set_title('All BHs')
ax[1].set_title('Central BHs > $10^6$ M$_\odot$')
ax[0].set_xlabel('$\log_{10}(M_\mathrm{BH} \ [\mathrm{M}_\odot])$')
ax[1].set_xlabel('$\log_{10}(M_\mathrm{BH} \ [\mathrm{M}_\odot])$')
ax[0].set_ylabel('$\log_{10}(\dot{M}_\mathrm{BH} \ [\mathrm{M}_\odot \ \mathrm{yr}^{-1}])$')
divider = make_axes_locatable(ax[1])
cax = divider.append_axes('right', size='5%', pad=0.05)
fig.colorbar(h[3], cax=cax, label='Number of BHs')

EddRatios = [f * (4 * np.pi * G * np.logspace(5, 11) * 1.989e33 * mp) / (epsilon_r * c * Thomson) 
             / 1.989e33 * 365.25 * 24 * 60 * 60 for f in [1e-7, 1e-5, 1e-3, 1e-1]]
for i in range(0, 2):
    ax[i].plot(np.log10(np.logspace(5, 11)), np.log10(EddRatios[0]), ls='-.', c='k', alpha=0.5, label='$f_\mathrm{Edd} = 10^{-7}$')
    ax[i].plot(np.log10(np.logspace(5, 11)), np.log10(EddRatios[1]), ls=':', c='k', alpha=0.5, label='$f_\mathrm{Edd} = 10^{-5}$')
    ax[i].plot(np.log10(np.logspace(5, 11)), np.log10(EddRatios[2]), ls='--', c='k', alpha=0.5, label='$f_\mathrm{Edd} = 10^{-3}$')
    ax[i].plot(np.log10(np.logspace(5, 11)), np.log10(EddRatios[3]), ls='-', c='k', alpha=0.5, label='$f_\mathrm{Edd} = 10^{-1}$')

ax[1].legend(frameon=False, loc='lower right')
fig.tight_layout()
fig.savefig('ex1b.pdf')
plt.show()

## Exercise 13.2

In [ ]:
# Plot:
fig, ax = plt.subplots(figsize=(8, 6))

h = ax.hist2d(np.log10(Mstellar[(CentOrSat == 0) * (Mbh > 1e6)]), np.log10(Mbh[(CentOrSat == 0) * (Mbh > 1e6)]), 
              bins=80, norm=mpl.colors.LogNorm(), cmap='plasma', rasterized=True)
ax.set_xlabel('$\log_{10}(M_\star \ [\mathrm{M}_\odot])$')
ax.set_ylabel('$\log_{10}(M_\mathrm{BH} \ [\mathrm{M_\odot}])$')
fig.colorbar(h[3], ax=ax, label='Number of BHs')

# Stellar mass bins:
MstellarBins = 10**h[1]
MstellarBins_mid = (MstellarBins[:-1] + MstellarBins[1:]) / 2

# Mean relation:
mean = [np.mean(Mbh[(CentOrSat == 0) * (Mbh > 1e6) * (Mstellar > MstellarBins[i]) * (Mstellar < MstellarBins[i+1])]) 
        for i in range(len(MstellarBins[:-1]))]
ax.plot(np.log10(MstellarBins_mid), np.log10(mean), ls=':', lw=2, c='k', label='Mean Relation')

# McConell & Ma (2013):
log10Mbh = 8.46 + 1.05 * np.log10(MstellarBins_mid / 1e11)
ax.plot(np.log10(MstellarBins_mid), log10Mbh, ls='-', lw=2, c='k', label='McConell & Ma (2013)')

ax.legend(frameon=False, loc='upper left')
fig.tight_layout()
fig.savefig('ex2.pdf')
plt.show()

## Exercise 13.3

In [ ]:
# Plot:
fig, ax = plt.subplots(1, 3, figsize=(12, 4))

# Masks:
mask_tot = (CentOrSat == 0) * (Mbh > 1e6)
mask_lum = mask_tot * (Lbol > 1e45)
mask_mod = mask_tot * (Lbol > 1e42) * (Lbol < 1e45)

# Fractions vs Stellar Mass:
bins_stellar = np.linspace(10, 13, 6)
bins_stellar_mid = (bins_stellar[:-1] + bins_stellar[1:])/2
N_tot, bin_edges = np.histogram(np.log10(Mstellar[mask_tot]), bins=bins_stellar)
N_lum, bin_edges = np.histogram(np.log10(Mstellar[mask_lum]), bins=bins_stellar)
N_mod, bin_edges = np.histogram(np.log10(Mstellar[mask_mod]), bins=bins_stellar)
f_lum = N_lum / N_tot
f_mod = N_mod / N_tot

ax[0].plot(bins_stellar_mid, f_lum, lw=2, marker='o')
ax[0].plot(bins_stellar_mid, f_mod, lw=2, marker='o')
ax[0].set_xlabel('$\log_{10}(M_\star \ [\mathrm{M}_\odot])$')
ax[0].set_ylabel('Fraction')
ax[0].set_yscale('log')

# Fractions vs SFR:
bins_sfr = np.linspace(-1.7, 3, 6)
bins_sfr_mid = (bins_sfr[:-1] + bins_sfr[1:])/2
N_tot, bin_edges = np.histogram(np.log10(SFR[mask_tot * (SFR > 0)]), bins=bins_sfr)
N_lum, bin_edges = np.histogram(np.log10(SFR[mask_lum * (SFR > 0)]), bins=bins_sfr)
N_mod, bin_edges = np.histogram(np.log10(SFR[mask_mod * (SFR > 0)]), bins=bins_sfr)
f_lum = N_lum / N_tot
f_mod = N_mod / N_tot

ax[1].plot(bins_sfr_mid, f_lum, lw=2, marker='o')
ax[1].plot(bins_sfr_mid, f_mod, lw=2, marker='o')
ax[1].set_xlabel('$\log_{10}(\mathrm{SFR} \ [\mathrm{M}_\odot \ \mathrm{yr}^{-1}])$')
ax[1].set_yscale('log')

# Fractions vs SFR:
sSFR = SFR / Mstellar
bins_ssfr = np.linspace(-13, -9, 6)
bins_ssfr_mid = (bins_ssfr[:-1] + bins_ssfr[1:])/2
N_tot, bin_edges = np.histogram(np.log10(sSFR[mask_tot * (SFR > 0)]), bins=bins_ssfr)
N_lum, bin_edges = np.histogram(np.log10(sSFR[mask_lum * (SFR > 0)]), bins=bins_ssfr)
N_mod, bin_edges = np.histogram(np.log10(sSFR[mask_mod * (SFR > 0)]), bins=bins_ssfr)
f_lum = N_lum / N_tot
f_mod = N_mod / N_tot

ax[2].plot(bins_ssfr_mid, f_lum, lw=2, marker='o', label='$>10^{45}$')
ax[2].plot(bins_ssfr_mid, f_mod, lw=2, marker='o', label='$10^{42}-10^{45}$')
ax[2].legend(fontsize=12, title_fontsize=12, frameon=False, title='$L_\mathrm{AGN} \ [\mathrm{erg \ s}^{-1}]$')
ax[2].set_xlabel('$\log_{10}(\mathrm{sSFR} \ [\mathrm{yr}^{-1}])$')
ax[2].set_yscale('log')

fig.tight_layout()
fig.savefig('ex3.pdf')
plt.show()

## Exercsie 13.4

In [ ]:
# Plot:
fig, ax = plt.subplots(1, 3, figsize=(12, 4), sharex=True, sharey=True)

# Masks:
mask_tot = (CentOrSat == 0) * (Mbh > 1e6) * (SFR > 0)
mask_lum = mask_tot * (Lbol > 1e45)
mask_mod = mask_tot * (Lbol > 1e42) * (Lbol < 1e45)

# Number of galaxies / fraction of (moderately) luminous AGN:
bins = [np.linspace(10, 13, 50), np.linspace(-1.7, 3, 50)]
H_tot, xedges, yedges = np.histogram2d(np.log10(Mstellar[mask_tot]), np.log10(SFR[mask_tot]), bins=bins)
H_lum, xedges, yedges = np.histogram2d(np.log10(Mstellar[mask_lum]), np.log10(SFR[mask_lum]), bins=bins)
H_mod, xedges, yedges = np.histogram2d(np.log10(Mstellar[mask_mod]), np.log10(SFR[mask_mod]), bins=bins)
X, Y = np.meshgrid(xedges, yedges)

pc = ax[0].pcolormesh(X, Y, H_tot.T, norm=mpl.colors.LogNorm(), cmap='plasma', rasterized=True)
fig.colorbar(pc, ax=ax[0], location='top', pad=0, label='Number of galaxies')
ax[0].set_xlabel('$\log_{10}(M_\star \ [\mathrm{M}_\odot])$')
ax[0].set_ylabel('$\log_{10}(\mathrm{SFR} \ [\mathrm{M}_\odot \ \mathrm{yr}^{-1}])$')

pc = ax[1].pcolormesh(X, Y, H_lum.T/H_tot.T, norm=mpl.colors.LogNorm(vmin=1e-2, vmax=1e0), cmap='plasma', rasterized=True)
fig.colorbar(pc, ax=ax[1], location='top', pad=0, label='Fraction of luminous AGN')
ax[1].set_xlabel('$\log_{10}(M_\star \ [\mathrm{M}_\odot])$')

pc = ax[2].pcolormesh(X, Y, H_mod.T/H_tot.T, norm=mpl.colors.LogNorm(vmin=1e-2, vmax=1e0), cmap='plasma', rasterized=True)
fig.colorbar(pc, ax=ax[2], location='top', pad=0, label='Fraction of moderately luminous AGN')
ax[2].set_xlabel('$\log_{10}(M_\star \ [\mathrm{M}_\odot])$')

# MS fit & Cano-Díaz et al. (2016):
fit = np.polyfit(np.log10(Mstellar[mask_tot * (Mstellar < 1e11) * (SFR > 1e0)]), np.log10(SFR[mask_tot  * (Mstellar < 1e11) * (SFR > 1e0)]), 1)
ms = fit[0] * bins[0] + fit[1]
for i in range(0, 3):
    ax[i].plot(bins[0], ms, c='k', lw=2, ls=':', label='Main Sequence Fit')
    ax[i].plot(bins[0], 0.81 * bins[0] - 8.34, c='k', lw=2, label='Cano-Díaz et al. (2016)')

ax[2].legend(fontsize=12, loc='lower right')

fig.tight_layout()
fig.savefig('ex4.pdf')
plt.show()